In [1]:
from elasticsearch import Elasticsearch 
from elasticsearch import helpers, Elasticsearch
import csv
import os
import glob
import pandas as pd
import re
import string
import itertools
import nltk
import time
from nltk.stem import PorterStemmer
ps =nltk.PorterStemmer()
from nltk.corpus import stopwords
import pickle
stops = set(stopwords.words("english")) 
from nltk.tokenize import word_tokenize

# Connect to the elastic cluster
es=Elasticsearch([{'host':'localhost','port':9200}])
es

<Elasticsearch([{'host': 'localhost', 'port': 9200}])>

In [3]:
prefix_path = 'C://Users//Kirthika//Desktop//PES//AIR-Final//AIR//Dataset'
extension = 'csv'
os.chdir(prefix_path)
filenames = glob.glob('*.{}'.format(extension))
i = 1
mapping = {}


In [ ]:
for file in filenames:
         complete_path = prefix_path + '\\' + str(file)
         with open(complete_path,encoding="utf-8") as f:
                reader = csv.DictReader(f)
                d_r = {}
                r = 0
                for row in reader:
                    print(reader)
                    if(r!=0):
                        d_r['snippet'] = row['Snippet']
                        id_row = str(file) + ":" + str(r)
                        mapping[i] = id_row
                        es.index(index="envn", doc_type="env", body=d_r, id=id_row)
                        i += 1
                    r+=1
                 #helpers.bulk(es, reader, index='my-index', doc_type='my-type')

In [ ]:
def es_search(query,result):
    
    result[query]={}
    result[query]['snippet']=[]
    result[query]['time']=0
    start=time.time()
    data=es.search(index="envn", body={"from":0, "size" : 5000 , "min_score":0, "query": { "match" :  {'snippet':query}}})
    for i in range(len(data['hits']['hits'])):
        result[query]['snippet'].append(data['hits']['hits'][i]['_source']['snippet'])
    end=time.time()
    result[query]['time']=end-start

In [ ]:

queryfile="sample_queries"
inputfile= open(queryfile,"r")
result={}
for line in (inputfile.read().split('\n')):
    es_search(line,result)

In [ ]:
resultsdf=pd.DataFrame.from_dict(result)
resultsdf

In [ ]:
import pickle

In [ ]:
with open('relevant_final-5000.pickle', 'wb') as handle:
    pickle.dump(resultsdf, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [ ]:
print(res['hits']['hits'][0]['_source']['snippet'])

In [ ]:
len((resultsdf['trump']['snippet'])